## TASK 1: Get a COVID-19 pandemic Wiki page using HTTP request

In [ ]:
# Installing importannt packages  for this project
install.packages("httr")
install.packages("rvest")

# Load the important packages
library(httr)
library(rvest)

In [16]:
get_wiki_covid19_page <- function() {
  # Define the base URL
  wiki_base_url <- "https://en.wikipedia.org/w/index.php"

  # Define query parameters as a list
  query_params <- list(title = "Template:COVID-19_testing_by_country")
  
  # Send HTTP GET request
  response <- GET(url = wiki_base_url, query = query_params)
  
  # Return the response
  return(response)
}
# Call the function and store the response
wiki_response <- get_wiki_covid19_page()
# Print the status of the request
print(status_code(wiki_response))
# View the first few lines of the retrieved HTML content
content(wiki_response, as = "text")


[1] 200


[1] "<!DOCTYPE html>\n<html class=\"client-nojs vector-feature-language-in-header-enabled vector-feature-language-in-main-page-header-disabled vector-feature-page-tools-pinned-disabled vector-feature-toc-pinned-clientpref-1 vector-feature-main-menu-pinned-disabled vector-feature-limited-width-clientpref-1 vector-feature-limited-width-content-enabled vector-feature-custom-font-size-clientpref-1 vector-feature-appearance-pinned-clientpref-1 vector-feature-night-mode-enabled skin-theme-clientpref-day vector-sticky-header-enabled vector-toc-available\" lang=\"en\" dir=\"ltr\">\n<head>\n<meta charset=\"UTF-8\">\n<title>Template:COVID-19 testing by country - Wikipedia</title>\n<script>(function(){var className=\"client-js vector-feature-language-in-header-enabled vector-feature-language-in-main-page-header-disabled vector-feature-page-tools-pinned-disabled vector-feature-toc-pinned-clientpref-1 vector-feature-main-menu-pinned-disabled vector-feature-limited-width-clientpref-1 vector-feature-limited-width-content-enabled vector-feature-custom-font-size-clientpref-1 vector-feature-appearance-pinned-clientpref-1 vector-feature-night-mode-enabled skin-theme-clientpref-day vector-sticky-header-enabled vector-toc-available\";var cookie=document.cookie.match(/(?:^|; )enwikimwclientpreferences=([^;]+)/);if(cookie){cookie[1].split('%2C').forEach(function(pref){className=className.replace(new RegExp('(^| )'+pref.replace(/-clientpref-\\w+$|[^\\w-]+/g,'')+'-clientpref-\\\\w+( |$)'),'$1'+pref+'$2');});}document.documentElement.className=className;}());RLCONF={\"wgBreakFrames\":false,\"wgSeparatorTransformTable\":[\"\",\"\"],\"wgDigitTransformTable\":[\"\",\"\"],\"wgDefaultDateFormat\":\"dmy\",\"wgMonthNames\":[\"\",\"January\",\"February\",\"March\",\"April\",\"May\",\"June\",\"July\",\"August\",\"September\",\"October\",\"November\",\"December\"],\"wgRequestId\":\"88d6719b-44ca-4f40-bbcb-312c7b37a725\",\"wgCanonicalNamespace\":\"Template\",\"wgCanonicalSpecialPageName\":false,\"wgNamespaceNumber\":10,\"wgPageName\":\"Template:COVID-19_testing_by_country\",\"wgTitle\":\"COVID-19 testing by country\",\"wgCurRevisionId\":1247585571,\"wgRevisionId\":1247585571,\"wgArticleId\":63303421,\"wgIsArticle\":true,\"wgIsRedirect\":false,\"wgAction\":\"view\",\"wgUserName\":null,\"wgUserGroups\":[\"*\"],\"wgCategories\":[\"CS1 Albanian-language sources (sq)\",\"CS1 French-language sources (fr)\",\"CS1 Portuguese-language sources (pt)\",\"CS1 Spanish-language sources (es)\",\"CS1 uses Armenian-language script (hy)\",\"CS1 Armenian-language sources (hy)\",\"CS1 German-language sources (de)\",\"CS1 Azerbaijani-language sources (az)\",\"CS1 uses Arabic-language script (ar)\",\"CS1 Arabic-language sources (ar)\",\"CS1 uses Russian-language script (ru)\",\"CS1 Russian-language sources (ru)\",\"CS1 Bosnian-language sources (bs)\",\"CS1 uses Bulgarian-language script (bg)\",\"CS1 Bulgarian-language sources (bg)\",\"CS1 uses Khmer-language script (km)\",\"CS1 Khmer-language sources (km)\",\"CS1 uses Chinese-language script (zh)\",\"CS1 Chinese-language sources (zh)\",\"CS1 Croatian-language sources (hr)\",\"CS1 uses Greek-language script (el)\",\"CS1 Greek-language sources (el)\",\"CS1 Czech-language sources (cs)\",\"CS1 Danish-language sources (da)\",\"CS1 uses Amharic-language script (am)\",\"CS1 Amharic-language sources (am)\",\"CS1 uses Georgian-language script (ka)\",\"CS1 Georgian-language sources (ka)\",\"CS1 Hungarian-language sources (hu)\",\"CS1 uses Hebrew-language script (he)\",\"CS1 Hebrew-language sources (he)\",\"CS1 Italian-language sources (it)\",\"CS1 uses Japanese-language script (ja)\",\"CS1 Japanese-language sources (ja)\",\"CS1 Kyrgyz-language sources (ky)\",\"CS1 Lao-language sources (lo)\",\"CS1 Latvian-language sources (lv)\",\"CS1 Lithuanian-language sources (lt)\",\"CS1 Malagasy-language sources (mg)\",\"CS1 Malay-language sources (ms)\",\"CS1 Romanian-language sources (ro)\",\"CS1 uses Mongolian-language script (mn)\",\"CS1 Mongolian-langu

# TASK 2: Extract COVID-19 testing data table from the wiki HTML page

In [21]:
# Read HTML content from the response
wiki_html <- read_html(wiki_response)

# Extract all table nodes from the HTML
table_nodes <- html_nodes(wiki_html, "table")

# Read the second table and convert it into a data frame
covid_testing_data <- html_table(table_nodes[2], fill = TRUE)

# Convert to data frame
covid_testing_df <- as.data.frame(covid_testing_data)

# Print the extracted data frame
print(covid_testing_df)

# TASK 3: Pre-process and export the extracted data frame

In [24]:
# Preprocessing function
preprocess_covid_data_frame <- function(data_frame) {
  
  shape <- dim(data_frame)
  # Remove the "World" row
  data_frame <- data_frame[!(data_frame$`Country.or.region` == "World"), ]
  # Remove the last row (assuming dataset has 172 rows, adjust if needed)
  data_frame <- data_frame[1:(nrow(data_frame) - 1), ]
  # Remove irrelevant columns
  data_frame["Ref."] <- NULL
  data_frame["Units.b."] <- NULL
  # Renaming columns for clarity
  names(data_frame) <- c("country", "date", "tested", "confirmed", 
                         "confirmed_tested_ratio", "tested_population_ratio", 
                         "confirmed_population_ratio")
  
  # Convert column data types
  data_frame$country <- as.factor(data_frame$country)
  data_frame$date <- as.factor(data_frame$date)
  data_frame$tested <- as.numeric(gsub(",", "", data_frame$tested))
  data_frame$confirmed <- as.numeric(gsub(",", "", data_frame$confirmed))
  data_frame$confirmed_tested_ratio <- as.numeric(gsub(",", "", data_frame$confirmed_tested_ratio))
  data_frame$tested_population_ratio <- as.numeric(gsub(",", "", data_frame$tested_population_ratio))
  data_frame$confirmed_population_ratio <- as.numeric(gsub(",", "", data_frame$confirmed_population_ratio))
  return(data_frame)
}

# Call the function to preprocess the extracted data
processed_covid_df <- preprocess_covid_data_frame(covid_testing_df)
# Print the summary of the processed data frame
print(summary(processed_covid_df))
# Define the file path
file_path <- "~/R_forDataScience/R_Basics/18covid.csv"
# Save the processed data frame to the specified path
write.csv(processed_covid_df, file_path, row.names = FALSE)
# Check if the file is successfully saved
print(file_path)
print(file.exists(file_path))  # TRUE if the file was successfully created

                country             date         tested         
 Afghanistan        :  1   2 Feb 2023 :  6   Min.   :     3880  
 Albania            :  1   1 Feb 2023 :  4   1st Qu.:   512037  
 Algeria            :  1   31 Jan 2023:  4   Median :  3029859  
 Andorra            :  1   1 Mar 2021 :  3   Mean   : 31377219  
 Angola             :  1   23 Jul 2021:  3   3rd Qu.: 12386725  
 Antigua and Barbuda:  1   29 Jan 2023:  3   Max.   :929349291  
 (Other)            :166   (Other)    :149                      
   confirmed        confirmed_tested_ratio tested_population_ratio
 Min.   :       0   Min.   : 0.00          Min.   :   0.006       
 1st Qu.:   37839   1st Qu.: 5.00          1st Qu.:   9.475       
 Median :  281196   Median :10.05          Median :  46.950       
 Mean   : 2508340   Mean   :11.25          Mean   : 175.504       
 3rd Qu.: 1278105   3rd Qu.:15.25          3rd Qu.: 156.500       
 Max.   :90749469   Max.   :46.80          Max.   :3223.000       
           

# TASK 4: Get a subset of the extracted data frame¶

In [27]:
# Read the processed COVID-19 data from the CSV file
covid_data <- read.csv("~/R_forDataScience/R_Basics/18covid.csv")

# Get rows 5 to 10 with only 'country' and 'confirmed' columns
subset_covid_data <- covid_data[5:10, c("country", "confirmed")]

# Print the subset
print(subset_covid_data)

               country confirmed
5               Angola     20981
6  Antigua and Barbuda       832
7            Argentina   9060495
8              Armenia    422963
9            Australia  10112229
10             Austria   5789991


# TASK 5: Calculate worldwide COVID testing positive ratio

In [30]:
# Get total confirmed cases worldwide
total_confirmed <- sum(covid_data$confirmed, na.rm = TRUE)

# Get total tested cases worldwide
total_tested <- sum(covid_data$tested, na.rm = TRUE)

# Calculate positive ratio
positive_ratio <- total_confirmed / total_tested

# Print results
print(paste("Total Confirmed Cases Worldwide:", total_confirmed))
print(paste("Total Tested Cases Worldwide:", total_tested))
print(paste("Worldwide COVID Testing Positive Ratio:", round(positive_ratio, 4)))

[1] "Total Confirmed Cases Worldwide: 431434555"
[1] "Total Tested Cases Worldwide: 5396881644"
[1] "Worldwide COVID Testing Positive Ratio: 0.0799"


# TASK 6: Get a country list which reported their testing data

In [33]:
# Extract the 'country' column
country_list <- covid_data$country

# Check the class of the column
print(paste("Class of country column:", class(country_list)))

# Convert the country column to character for sorting
country_list <- as.character(country_list)

# Sort the country names in A to Z order
sorted_countries_AtoZ <- sort(country_list)

# Sort the country names in Z to A order
sorted_countries_ZtoA <- sort(country_list, decreasing = TRUE)

# Print the sorted country list in Z to A order
print("Sorted countries (Z to A):")
print(sorted_countries_ZtoA)

[1] "Class of country column: character"
[1] "Sorted countries (Z to A):"
  [1] "Zimbabwe"               "Zambia"                 "Vietnam"               
  [4] "Venezuela"              "Uzbekistan"             "Uruguay"               
  [7] "United States"          "United Kingdom"         "United Arab Emirates"  
 [10] "Ukraine"                "Uganda"                 "Turkey"                
 [13] "Tunisia"                "Trinidad and Tobago"    "Togo"                  
 [16] "Thailand"               "Tanzania"               "Taiwan[m]"             
 [19] "Switzerland[l]"         "Sweden"                 "Sudan"                 
 [22] "Sri Lanka"              "Spain"                  "South Sudan"           
 [25] "South Korea"            "South Africa"           "Slovenia"              
 [28] "Slovakia"               "Singapore"              "Serbia"                
 [31] "Senegal"                "Saudi Arabia"           "San Marino"            
 [34] "Saint Vincent"          "Sai

# TASK 7: Identify countries names with a specific pattern

In [36]:
# Use grep with regular expression to find country names starting with "United"
matched_countries <- grep("^United.+", country_list, value = TRUE)

# Print the matched country names
print("Countries starting with 'United':")
print(matched_countries)

[1] "Countries starting with 'United':"
[1] "United Arab Emirates" "United Kingdom"       "United States"       


# TASK 8: Pick two countries you are interested, and then review their testing data

In [39]:
# Define the countries of interest
countries <- c("Pakistan", "India")

# Filter using Base R subset() and select relevant columns
comparison_data <- subset(covid_data, country %in% countries, 
                          select = c("country", "confirmed", "confirmed_population_ratio"))

# Print the result
print(comparison_data)

     country confirmed confirmed_population_ratio
73     India  43585554                      31.70
124 Pakistan    588728                       0.27


# TASK 9: Compare which one of the selected countries has a larger ratio of confirmed cases to population

In [42]:
# Extract values
ratio_pakistan <- comparison_data[comparison_data$country == "Pakistan", "confirmed_population_ratio"]
ratio_india <- comparison_data[comparison_data$country == "India", "confirmed_population_ratio"]

# Compare and print the result
if (ratio_pakistan > ratio_india) {
  print("Pakistan has a higher confirmed cases to population ratio.")
} else if (ratio_pakistan < ratio_india) {
  print("India has a higher confirmed cases to population ratio.")
} else {
  print("Both countries have the same confirmed cases to population ratio.")
}

[1] "India has a higher confirmed cases to population ratio."


# TASK 10: Find countries with confirmed to population ratio rate less than a threshold

In [45]:
# Define the threshold
threshold <- 0.01  # 0.01 OR 1%

# Filter countries where confirmed.population.ratio is below the threshold
low_risk_countries <- subset(covid_data, confirmed_population_ratio < threshold, 
                             select = c("country", "confirmed_population_ratio"))

# Print the result
print(low_risk_countries)

        country confirmed_population_ratio
28      Burundi                    0.00740
34     China[c]                    0.00610
89         Laos                    0.00063
119 North Korea                    0.00000
156    Tanzania                    0.00085
